In [1]:
from collections import deque
from datetime import datetime
import os
import time
import requests
import json

import pickle
from pathlib import Path

import traceback

def print_log(*args):
    print(f"[{str(datetime.now())[:-3]}] ", end="")
    print(*args)

def get_all_app_id():
    # get all app id
    req = requests.get("https://api.steampowered.com/ISteamApps/GetAppList/v2/")

    if (req.status_code != 200):
        print_log("Failed to get all games on steam.")
        return
    
    try:
        data = req.json()
    except Exception as e:
        traceback.print_exc(limit=5)
        return {}
    
    apps_data = data['applist']['apps']

    apps_ids = []

    for app in apps_data:
        appid = app['appid']
        name = app['name']
        
        # skip apps that have empty name
        if not name:
            continue

        apps_ids.append(appid)

    return apps_ids



def save_checkpoints(checkpoint_folder, apps_dict_filename_prefix, exc_apps_filename_prefix, error_apps_filename_prefix, apps_dict, excluded_apps_list, error_apps_list):
    if not checkpoint_folder.exists():
        checkpoint_folder.mkdir(parents=True)

    save_path = checkpoint_folder.joinpath(
        apps_dict_filename_prefix + f'-ckpt-fin.p'
    ).resolve()

    save_path2 = checkpoint_folder.joinpath(
        exc_apps_filename_prefix + f'-ckpt-fin.p'
    ).resolve()
    
    save_path3 = checkpoint_folder.joinpath(
        error_apps_filename_prefix + f'-ckpt-fin.p'
    ).resolve()

    save_pickle(save_path, apps_dict)
    print_log(f'Successfully create app_dict checkpoint: {save_path}')

    save_pickle(save_path2, excluded_apps_list)
    print_log(f"Successfully create excluded apps checkpoint: {save_path2}")

    save_pickle(save_path3, error_apps_list)
    print_log(f"Successfully create error apps checkpoint: {save_path3}")

    print()


def load_pickle(path_to_load:Path) -> dict:
    obj = pickle.load(open(path_to_load, "rb"))
    
    return obj

def save_pickle(path_to_save:Path, obj):
    with open(path_to_save, 'wb') as handle:
        pickle.dump(obj, handle, protocol=pickle.HIGHEST_PROTOCOL)

def check_latest_checkpoints(checkpoint_folder, apps_dict_filename_prefix, exc_apps_filename_prefix, error_apps_filename_prefix):
    # app_dict
    all_pkl = []

    # get all pickle files in the checkpoint folder    
    for root, dirs, files in os.walk(checkpoint_folder):
        all_pkl = list(map(lambda f: Path(root, f), files))
        all_pkl = [p for p in all_pkl if p.suffix == '.p']
        break
            
    # create a list to store all the checkpoint files
    # then sort them
    # the latest checkpoint file for each of the object is the last element in each of the lists
    apps_dict_ckpt_files = [f for f in all_pkl if apps_dict_filename_prefix in f.name and "ckpt" in f.name]
    exc_apps_list_ckpt_files = [f for f in all_pkl if exc_apps_filename_prefix in f.name and "ckpt" in f.name]
    error_apps_ckpt_files = [f for f in all_pkl if error_apps_filename_prefix in f.name and 'ckpt' in f.name]

    apps_dict_ckpt_files.sort()
    exc_apps_list_ckpt_files.sort()
    error_apps_ckpt_files.sort()

    latest_apps_dict_ckpt_path = apps_dict_ckpt_files[-1] if apps_dict_ckpt_files else None
    latest_exc_apps_list_ckpt_path = exc_apps_list_ckpt_files[-1] if exc_apps_list_ckpt_files else None
    latest_error_apps_list_ckpt_path = error_apps_ckpt_files[-1] if error_apps_ckpt_files else None

    return latest_apps_dict_ckpt_path, latest_exc_apps_list_ckpt_path, latest_error_apps_list_ckpt_path

def main():
    print_log("Started Steam scraper process", os.getpid())


    apps_dict_filename_prefix = 'apps_dict'
    exc_apps_filename_prefix = 'excluded_apps_list'
    error_apps_filename_prefix = 'error_apps_list'

    apps_dict = {}
    excluded_apps_list = []
    error_apps_list = []

    all_app_ids = get_all_app_id()

    print_log('Total number of apps on steam:', len(all_app_ids))

    # path = project directory (i.e. steam_data_scraping)/checkpoints
    checkpoint_folder = Path('checkpoints').resolve()

    print_log('Checkpoint folder:', checkpoint_folder)

    if not checkpoint_folder.exists():
        print_log(f'Fail to find checkpoint folder: {checkpoint_folder}')
        print_log(f'Start at blank.')

        checkpoint_folder.mkdir(parents=True)

    latest_apps_dict_ckpt_path, latest_exc_apps_list_ckpt_path, latest_error_apps_list_ckpt_path = check_latest_checkpoints(checkpoint_folder, apps_dict_filename_prefix, exc_apps_filename_prefix, error_apps_filename_prefix)

    if latest_apps_dict_ckpt_path:
        apps_dict = load_pickle(latest_apps_dict_ckpt_path)
        print_log('Successfully load apps_dict checkpoint:', latest_apps_dict_ckpt_path)
        print_log(f'Number of apps in apps_dict: {len(apps_dict)}')
    
    if latest_exc_apps_list_ckpt_path:
        excluded_apps_list = load_pickle(latest_exc_apps_list_ckpt_path)
        print_log("Successfully load excluded_apps_list checkpoint:", latest_exc_apps_list_ckpt_path)
        print_log(f'Number of apps in excluded_apps_list: {len(excluded_apps_list)}')

    if latest_error_apps_list_ckpt_path:
        error_apps_list = load_pickle(latest_error_apps_list_ckpt_path)
        print_log("Successfully load error_apps_list checkpoint:", latest_error_apps_list_ckpt_path)
        print_log(f'Number of apps in error_apps_list: {len(error_apps_list)}')

    # remove app_ids that already scrapped or excluded or error
    all_app_ids = set(all_app_ids) \
            - set(map(int, set(apps_dict.keys()))) \
            - set(map(int, excluded_apps_list)) \
            - set(map(int, error_apps_list))
        
    # first get remaining apps
    apps_remaining_deque = deque(set(all_app_ids))

    
    print('Number of remaining apps:', len(apps_remaining_deque))

    i = 0
    while len(apps_remaining_deque) > 0:
        appid = apps_remaining_deque.popleft()

        # test whether the game exists or not
        # by making request to get the details of the app
        try:
            appdetails_req = requests.get(f"https://store.steampowered.com/api/appdetails?appids={appid}")

            if appdetails_req.status_code == 200:
                appdetails = appdetails_req.json()
                appdetails = appdetails[str(appid)]

            elif appdetails_req.status_code == 429:
                print_log(f'Too many requests. Put App ID {appid} back to deque. Sleep for 10 sec')
                apps_remaining_deque.appendleft(appid)
                time.sleep(10)
                continue


            elif appdetails_req.status_code == 403:
                print_log(f'Forbidden to access. Put App ID {appid} back to deque. Sleep for 5 min.')
                apps_remaining_deque.appendleft(appid)
                time.sleep(5 * 60)
                continue

            else:
                print_log("ERROR: status code:", appdetails_req.status_code)
                print_log(f"Error in App Id: {appid}. Put the app to error apps list.")
                error_apps_list.append(appid)
                continue
                
        except:
            print_log(f"Error in decoding app details request. App id: {appid}")

            traceback.print_exc(limit=5)
            appdetails = {'success':False}
            print()

        # not success -> the game does not exist anymore
        # add the app id to excluded app id list
        if appdetails['success'] == False:
            excluded_apps_list.append(appid)
            print_log(f'No successful response. Add App ID: {appid} to excluded apps list')
            continue

        appdetails_data = appdetails['data']

        appdetails_data['appid'] = appid     

        apps_dict[appid] = appdetails_data
        print_log(f"Successfully get content of App ID: {appid}")

        i += 1
        # for each 2500, save a ckpt
        if i >= 2500:
            save_checkpoints(checkpoint_folder, apps_dict_filename_prefix, exc_apps_filename_prefix, error_apps_filename_prefix, apps_dict, excluded_apps_list, error_apps_list)
            i = 0

    # save checkpoints at the end
    save_checkpoints(checkpoint_folder, apps_dict_filename_prefix, exc_apps_filename_prefix, error_apps_filename_prefix, apps_dict, excluded_apps_list, error_apps_list)

    print_log(f"Total number of valid apps: {len(apps_dict)}")
    print_log(f"Total number of skipped apps: {len(excluded_apps_list)}")
    print_log(f"Total number of error apps: {len(error_apps_list)}")

    print_log('Successful run. Program Terminates.')

if __name__ == '__main__':
    main()

[2024-09-21 19:42:02.427] Started Steam scraper process 28020
[2024-09-21 19:42:03.440] Total number of apps on steam: 214587
[2024-09-21 19:42:03.444] Checkpoint folder: C:\Users\wesdu\GA_DAB_812_python\Capstone\checkpoints
[2024-09-21 19:42:17.919] Successfully load apps_dict checkpoint: C:\Users\wesdu\GA_DAB_812_python\Capstone\checkpoints\apps_dict-ckpt-fin.p
[2024-09-21 19:42:17.919] Number of apps in apps_dict: 137500
[2024-09-21 19:42:17.935] Successfully load excluded_apps_list checkpoint: C:\Users\wesdu\GA_DAB_812_python\Capstone\checkpoints\excluded_apps_list-ckpt-fin.p
[2024-09-21 19:42:17.935] Number of apps in excluded_apps_list: 13017
[2024-09-21 19:42:17.939] Successfully load error_apps_list checkpoint: C:\Users\wesdu\GA_DAB_812_python\Capstone\checkpoints\error_apps_list-ckpt-fin.p
[2024-09-21 19:42:17.939] Number of apps in error_apps_list: 47
Number of remaining apps: 64077
[2024-09-21 19:42:18.660] Successfully get content of App ID: 2344680
[2024-09-21 19:42:19.314

Traceback (most recent call last):
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connectionpool.py", line 468, in _make_request
    self._validate_conn(conn)
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connectionpool.py", line 1097, in _validate_conn
    conn.connect()
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connection.py", line 642, in connect
    sock_and_verified = _ssl_wrap_socket_and_match_hostname(
                        ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connection.py", line 783, in _ssl_wrap_socket_and_match_hostname
    ssl_sock = ssl_wrap_socket(
               ^^^^^^^^^^^^^^^^
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\util\ssl_.py", line 471, in ssl_wrap_socket
    ssl_sock = _ssl_wrap_socket_impl(sock, context, tls_in_tls, server_hostname)
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
ssl.SSLEOFError: [SSL: UNEXPECT

[2024-09-22 05:47:52.232] Successfully get content of App ID: 1468850
[2024-09-22 05:47:53.255] Successfully get content of App ID: 1993140
[2024-09-22 05:47:54.275] Successfully get content of App ID: 944570
[2024-09-22 05:47:55.210] Successfully get content of App ID: 1468860
[2024-09-22 05:47:56.115] Successfully get content of App ID: 1993150
[2024-09-22 05:47:57.387] Successfully get content of App ID: 2517440
[2024-09-22 05:47:58.139] Successfully get content of App ID: 420290
[2024-09-22 05:47:58.885] Successfully get content of App ID: 3041730
[2024-09-22 05:47:59.607] Successfully get content of App ID: 1468870
[2024-09-22 05:48:00.455] Successfully get content of App ID: 1993160
[2024-09-22 05:48:01.275] Successfully get content of App ID: 3041740
[2024-09-22 05:48:02.450] Successfully get content of App ID: 420300
[2024-09-22 05:48:03.331] Successfully get content of App ID: 944590
[2024-09-22 05:48:04.141] Successfully get content of App ID: 1468880
[2024-09-22 05:48:04.951

Traceback (most recent call last):
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connectionpool.py", line 468, in _make_request
    self._validate_conn(conn)
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connectionpool.py", line 1097, in _validate_conn
    conn.connect()
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connection.py", line 642, in connect
    sock_and_verified = _ssl_wrap_socket_and_match_hostname(
                        ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connection.py", line 783, in _ssl_wrap_socket_and_match_hostname
    ssl_sock = ssl_wrap_socket(
               ^^^^^^^^^^^^^^^^
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\util\ssl_.py", line 471, in ssl_wrap_socket
    ssl_sock = _ssl_wrap_socket_impl(sock, context, tls_in_tls, server_hostname)
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
ssl.SSLEOFError: [SSL: UNEXPECT

[2024-09-22 09:31:50.139] Successfully get content of App ID: 944630
[2024-09-22 09:31:51.366] Successfully get content of App ID: 1468920
[2024-09-22 09:31:52.296] Successfully get content of App ID: 1993210
[2024-09-22 09:31:53.266] Successfully get content of App ID: 2517500
[2024-09-22 09:31:54.112] Successfully get content of App ID: 944640
[2024-09-22 09:31:54.939] Successfully get content of App ID: 1468930
[2024-09-22 09:31:56.069] Successfully get content of App ID: 2517510
[2024-09-22 09:31:57.056] Successfully get content of App ID: 420360
[2024-09-22 09:31:57.975] Successfully get content of App ID: 944650
[2024-09-22 09:31:58.895] Successfully get content of App ID: 1468940
[2024-09-22 09:31:59.915] Successfully get content of App ID: 3041810
[2024-09-22 09:32:00.782] Successfully get content of App ID: 420370
[2024-09-22 09:32:01.512] Successfully get content of App ID: 944660
[2024-09-22 09:32:02.258] Successfully get content of App ID: 1468950
[2024-09-22 09:32:03.251] 

...

[2024-09-24 11:12:47.310] Error in decoding app details request. App id: 2602200

[2024-09-24 11:12:47.325] No successful response. Add App ID: 2602200 to excluded apps list


Traceback (most recent call last):
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connection.py", line 203, in _new_conn
    sock = connection.create_connection(
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\util\connection.py", line 85, in create_connection
    raise err
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\util\connection.py", line 73, in create_connection
    sock.connect(sa)
TimeoutError: [WinError 10060] A connection attempt failed because the connected party did not properly respond after a period of time, or established connection failed because connected host has failed to respond

The above exception was the direct cause of the following exception:

Traceback (most recent call last):
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connectionpool.py", line 791, in urlopen
    response = self._make_request(
               ^^^^^^^^^^^^^^^^^^^
  File "C:\Users\wesdu\anaconda3\Lib\sit

[2024-09-24 11:12:55.420] No successful response. Add App ID: 2340060 to excluded apps list
[2024-09-24 11:13:07.879] Successfully get content of App ID: 3126490
[2024-09-24 11:13:08.609] Successfully get content of App ID: 2864350
[2024-09-24 11:13:09.265] Successfully get content of App ID: 1029340
[2024-09-24 11:13:09.886] Successfully get content of App ID: 767200
[2024-09-24 11:13:10.520] Successfully get content of App ID: 2602210
[2024-09-24 11:13:11.108] Successfully get content of App ID: 1815780
[2024-09-24 11:13:11.774] Successfully get content of App ID: 505060
[2024-09-24 11:13:12.571] Successfully get content of App ID: 1029350
[2024-09-24 11:13:13.179] Successfully get content of App ID: 1029351
[2024-09-24 11:13:13.787] Successfully get content of App ID: 2864360
[2024-09-24 11:13:14.432] Successfully get content of App ID: 242920
[2024-09-24 11:13:15.193] Successfully get content of App ID: 1553640
[2024-09-24 11:13:15.950] Successfully get content of App ID: 1029352
[

Traceback (most recent call last):
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connectionpool.py", line 791, in urlopen
    response = self._make_request(
               ^^^^^^^^^^^^^^^^^^^
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connectionpool.py", line 492, in _make_request
    raise new_e
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connectionpool.py", line 468, in _make_request
    self._validate_conn(conn)
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connectionpool.py", line 1097, in _validate_conn
    conn.connect()
  File "C:\Users\wesdu\anaconda3\Lib\site-packages\urllib3\connection.py", line 642, in connect
    sock_and_verified = _ssl_wrap_socket_and_match_hostname(
                        ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host

During handling of the above exception, another exception occurred:

Traceback (most recen

[2024-09-24 14:40:31.518] Successfully get content of App ID: 1037370
[2024-09-24 14:40:32.754] Successfully get content of App ID: 1561660
[2024-09-24 14:40:33.638] Successfully get content of App ID: 1299520
[2024-09-24 14:40:34.492] No successful response. Add App ID: 2610240 to excluded apps list
[2024-09-24 14:40:35.409] Successfully get content of App ID: 1823810
[2024-09-24 14:40:36.550] Successfully get content of App ID: 513091
[2024-09-24 14:40:37.472] Successfully get content of App ID: 513090
[2024-09-24 14:40:38.867] Successfully get content of App ID: 1037380
[2024-09-24 14:40:40.119] Successfully get content of App ID: 513092
[2024-09-24 14:40:41.179] Successfully get content of App ID: 513095
[2024-09-24 14:40:42.696] Successfully get content of App ID: 513096
[2024-09-24 14:40:43.715] Successfully get content of App ID: 513093
[2024-09-24 14:40:44.500] Successfully get content of App ID: 513094
[2024-09-24 14:40:45.281] Successfully get content of App ID: 2348100
[2024

In [2]:
import pickle
from pathlib import Path
import os

checkpoint_folder = Path("checkpoints")

apps_dict_filename_prefix = 'apps_dict'
exc_apps_filename_prefix = 'excluded_apps_list'
error_apps_filename_prefix = 'error_apps_list'

apps_dict = {}
excluded_apps_list = []
error_apps_list = []

In [3]:
def check_latest_checkpoints(checkpoint_folder, apps_dict_filename_prefix, exc_apps_filename_prefix, error_apps_filename_prefix):
    # app_dict
    all_pkl = []
    
    for root, dirs, files in os.walk(checkpoint_folder):
        all_pkl = list(map(lambda f: Path(root, f), files))
        all_pkl = [p for p in all_pkl if p.suffix == '.p']
        break
            
    apps_dict_ckpt_files = [f for f in all_pkl if apps_dict_filename_prefix in f.name and "ckpt" in f.name]
    exc_apps_list_ckpt_files = [f for f in all_pkl if exc_apps_filename_prefix in f.name and "ckpt" in f.name]
    error_apps_ckpt_files = [f for f in all_pkl if error_apps_filename_prefix in f.name and 'ckpt' in f.name]

    apps_dict_ckpt_files.sort()
    exc_apps_list_ckpt_files.sort()
    error_apps_ckpt_files.sort()

    latest_apps_dict_ckpt_path = apps_dict_ckpt_files[-1] if apps_dict_ckpt_files else None
    latest_exc_apps_list_ckpt_path = exc_apps_list_ckpt_files[-1] if exc_apps_list_ckpt_files else None
    latest_error_apps_list_ckpt_path = error_apps_ckpt_files[-1] if error_apps_ckpt_files else None

    return latest_apps_dict_ckpt_path, latest_exc_apps_list_ckpt_path, latest_error_apps_list_ckpt_path

In [4]:
if not checkpoint_folder.exists():
    print(f'Fail to find checkpoint folder: {checkpoint_folder}')
    print(f'Start at blank.')

In [5]:
latest_apps_dict_ckpt_path, latest_exc_apps_list_ckpt_path, latest_error_apps_list_ckpt_path = check_latest_checkpoints(checkpoint_folder, apps_dict_filename_prefix, exc_apps_filename_prefix, error_apps_filename_prefix)

if latest_apps_dict_ckpt_path:
    apps_dict = load_pickle(latest_apps_dict_ckpt_path)
    print('Successfully load apps_dict checkpoint:', latest_apps_dict_ckpt_path)
    print(f'Number of apps in apps_dict: {len(apps_dict)}')

if latest_exc_apps_list_ckpt_path:
    excluded_apps_list = load_pickle(latest_exc_apps_list_ckpt_path)
    print("Successfully load excluded_apps_list checkpoint:", latest_exc_apps_list_ckpt_path)
    print(f'Number of apps in excluded_apps_list: {len(excluded_apps_list)}')

if latest_error_apps_list_ckpt_path:
    error_apps_list = load_pickle(latest_error_apps_list_ckpt_path)
    print("Successfully load error_apps_list checkpoint:", latest_error_apps_list_ckpt_path)
    print(f'Number of apps in error_apps_list: {len(error_apps_list)}')

Successfully load apps_dict checkpoint: checkpoints\apps_dict-ckpt-fin.p
Number of apps in apps_dict: 196724
Successfully load excluded_apps_list checkpoint: checkpoints\excluded_apps_list-ckpt-fin.p
Number of apps in excluded_apps_list: 17849
Successfully load error_apps_list checkpoint: checkpoints\error_apps_list-ckpt-fin.p
Number of apps in error_apps_list: 68
